In [4]:
import os,re,difflib,Levenshtein,time,json

# 重要!!! 范围
old_problems_range = "1:999999"
threshold = 0.85

# 待比对的文件
filename = r"C:\Users\weiye\Documents\wwy sync\临时工作区\空中课堂第六批.tex"

#生成数码列表, 逗号分隔每个区块, 区块内部用:表示整数闭区间
def generate_number_set(string):
    string = re.sub(r"[\n\s]","",string)
    string_list = string.split(",")
    numbers_list = []
    for s in string_list:
        if not ":" in s:
            numbers_list.append(s.zfill(6))
        else:
            start,end = s.split(":")
            for ind in range(int(start),int(end)+1):
                numbers_list.append(str(ind).zfill(6))
    return numbers_list

#字符串预处理
def pre_treating(string):
    string = re.sub(r"\\begin\{center\}[\s\S]*?\\end\{center\}","",string)
    string = re.sub(r"(bracket\{\d+\})|(blank\{\d+\})|(fourch)|(twoch)|(onech)|(mathrm)|(text)","",string)
    string = re.sub(r"[\s\\\{\}\$\(\)\[\]]","",string)
    string = re.sub(r"[\n\t]","",string)
    string = re.sub(r"(displaystyle)|(overrightarrow)","",string)
    string = re.sub(r"[,\.:;?]","",string)
    return string

#difflab字符串比较
def difflab_get_equal_rate(str1, str2):
    return difflib.SequenceMatcher(None, str1, str2).ratio()

#Levenshtein jaro字符串比较
def jaro_get_equal_rate(str1,str2):
    return Levenshtein.jaro(str1,str2)

#Levenshtein 字符串比较
def Lev_get_equal_rate(str1,str2):
    return Levenshtein.ratio(str1,str2)

def GenerateProblemListFromString(data):
    try:
        data = re.findall(r"\\begin\{document\}([\s\S]*?)\\end\{document\}",problems_string)[0]
    except:
        pass
    data = re.sub(r"\n{2,}","\n",data)
    data = re.sub(r"\\item",r"\\enditem\\item",data)
    data = re.sub(r"\\end\{enumerate\}",r"\\enditem",data)
    ProblemList_raw = [p.strip() for p in re.findall(r"\\item([\s\S]*?)\\enditem",data)]
    ProblemsList = []
    for p in ProblemList_raw:
        startpos = data.index(p)
        tempdata = data[:startpos]
        suflist = re.findall(r"\n\%[\dA-Za-z]+",tempdata)
        if len(suflist) > 0:
            suffix = suflist[-1].replace("%","").strip()
        else:
            suffix = ""
        ProblemsList.append((p,suffix))
    return ProblemsList


#指定对比方法
sim_test = jaro_get_equal_rate

#读入题库
with open(r"../题库0.3/Problems.json","r",encoding = "utf8") as f:
    database = f.read()
pro_dict = json.loads(database)

with open(filename,"r",encoding="u8") as f:
    newdatabase = f.read()
new_pro_list = GenerateProblemListFromString(newdatabase)

pro_dict_treated = {}
idrange_raw = generate_number_set(old_problems_range)
idrange = [id for id in pro_dict if id in idrange_raw]
for p in idrange:
    pro_dict_treated[p] = pre_treating(pro_dict[p]["content"])

new_dict_treated = {}
for i in range(len(new_pro_list)):
    new_dict_treated[i+1] = pre_treating(new_pro_list[i][0])

for i in new_dict_treated:
    new_p = new_dict_treated[i]
    maxsim = 0
    for p in pro_dict_treated:
        old_p = pro_dict_treated[p]
        sim = sim_test(new_p,old_p)
        if sim > maxsim:
            maxsim = sim
            argmax = p
    print("%.3f\t%d\t%s" %(maxsim,i,argmax))
    # print("\n新题: %s" %new_pro_list[i-1][0])
    # print("\n原题: %s\n\n\n" %pro_dict[]["content"])



1.000	1	004884
1.000	2	003673
0.903	3	000506
0.984	4	003665
0.921	5	012805
0.949	6	011578
0.987	7	011716
0.987	8	011674
0.867	9	000041
0.939	10	002911
0.876	11	011630
0.785	12	002858
0.990	13	011636
0.848	14	011186
0.763	15	011186
0.662	16	003625
0.971	17	011687
0.910	18	011712
0.685	19	003857
0.887	20	012107
1.000	21	011594
0.803	22	040098
1.000	23	011708
1.000	24	011724
1.000	25	011639
0.819	26	012756
1.000	27	011670
1.000	28	011608
0.995	29	011728
0.780	30	001553
0.876	31	009993
0.948	32	003638
0.628	33	003607
0.702	34	012316
0.686	35	022043
0.671	36	021435
0.957	37	011611
0.551	38	040015
0.935	39	012448
1.000	40	011648
1.000	41	011671
0.665	42	000387
0.777	43	003624
0.993	44	003666
1.000	45	012195
0.942	46	009988
1.000	47	011696
1.000	48	011631
0.602	49	004391
0.879	50	010710
1.000	51	011721
0.903	52	013057
0.799	53	009074
0.984	54	011686
0.975	55	011718
0.993	56	003733
1.000	57	000629
1.000	58	011697
0.998	59	011736
0.994	60	011700
1.000	61	003674
0.632	62	007439
0.986	63	012746
0

In [3]:
len(idrange)

999999